# Импорты

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
cd drive/MyDrive/Курсовая

/content/drive/MyDrive/Курсовая


In [ ]:
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
import re
import random
import os
import math
import pickle

import matplotlib.pyplot as plt
from tqdm.notebook import tqdm

from sklearn.model_selection import train_test_split
from sklearn.metrics import f1_score
from sklearn.decomposition import LatentDirichletAllocation
from sklearn.feature_extraction.text import CountVectorizer

import transformers
from transformers import BertForSequenceClassification, AdamW, BertConfig,BertTokenizer,get_linear_schedule_with_warmup
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, random_split
from torch.nn import CrossEntropyLoss

In [ ]:
def seed_everything(seed: int):
    random.seed(seed)
    os.environ['PYTHONHASHSEED'] = str(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = True

seed_everything(42)

# Подготовка

In [ ]:
df = pd.read_csv('sentiment140_100000.csv')

In [ ]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
device

device(type='cuda', index=0)

In [ ]:
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

In [ ]:
# словарь с эмбеддингами
with open('knowledge.pickle', 'rb') as f:
  knowledge_dct = pickle.load(f)

In [ ]:
res_dct = {}

# Функции

In [ ]:
def get_dataloaders(tokenizer, text_column, knowledge_dct=None, user_embedding_dim=None):
  """
  Функция для получения даталоадеров, чтобы обучать и тестировать модель
  Может создавать даталоадеры, учитывая доп. знание
  """
  # вычислим максимальную длину, добавляем 2, так как еще [CLS] и [SEP]
  max_length = max(df[text_column].apply(lambda x: len(x.split(' '))).value_counts().index) + 2

  # токенизируем train, val и test
  encoder_train = tokenizer.batch_encode_plus(
      df[df["data_type"]=='train'][text_column].values,
      add_special_tokens = True,
      return_attention_mask = True,
      truncation = True,
      padding = 'max_length',
      max_length = max_length,
      return_tensors = 'pt'
      )

  encoder_val = tokenizer.batch_encode_plus(
      df[df["data_type"]=='val'][text_column].values,
      add_special_tokens = True,
      return_attention_mask = True,
      truncation = True,
      padding = 'max_length',
      max_length = max_length,
      return_tensors = 'pt'
      )

  encoder_test = tokenizer.batch_encode_plus(
      df[df["data_type"]=='test'][text_column].values,
      add_special_tokens = True,
      return_attention_mask = True,
      truncation = True,
      padding = 'max_length',
      max_length = max_length,
      return_tensors = 'pt'
      )

  input_ids_train = encoder_train['input_ids']
  attention_masks_train = encoder_train["attention_mask"]
  labels_train = torch.tensor(df[df['data_type']=='train'].target.values)

  input_ids_val = encoder_val['input_ids']
  attention_masks_val = encoder_val["attention_mask"]
  labels_val = torch.tensor(df[df['data_type']=='val'].target.values)

  input_ids_test = encoder_test['input_ids']
  attention_masks_test = encoder_test["attention_mask"]
  labels_test = torch.tensor(df[df['data_type']=='test'].target.values)

  # создаем датасеты, учитывая доп. знание, если оно есть
  if knowledge_dct is not None:
    # создадим эмбеддинг усредненный по всем пользователям, если вдруг в словаре
    # не окажется пользователя (на случай val и test)
    no_embedding = np.zeros(user_embedding_dim)
    for user, embedding in knowledge_dct.items():
      no_embedding += embedding
    no_embedding = no_embedding/len(knowledge_dct)

    numerical_train = torch.tensor([np.array(knowledge_dct[user]) for user in df[df["data_type"]=='train'].user.values]).float()
    numerical_val = torch.tensor([np.array(knowledge_dct[user]) for user in df[df["data_type"]=='val'].user.values]).float()
    numerical_test = torch.tensor([np.array(knowledge_dct[user]) for user in df[df["data_type"]=='test'].user.values]).float()

    data_train = TensorDataset(input_ids_train, attention_masks_train, labels_train, numerical_train)
    data_test = TensorDataset(input_ids_test, attention_masks_test,labels_test, numerical_test)
    data_val = TensorDataset(input_ids_val, attention_masks_val,labels_val, numerical_val)

  # если доп. знания нет
  else:
    data_train = TensorDataset(input_ids_train, attention_masks_train, labels_train)
    data_test = TensorDataset(input_ids_test, attention_masks_test,labels_test)
    data_val = TensorDataset(input_ids_val, attention_masks_val,labels_val)

  # создаем даталоадеры с размером батча = 32
  dataloader_train = DataLoader(
    data_train,
    sampler= RandomSampler(data_train),
    batch_size=32
  )

  dataloader_val = DataLoader(
      data_val,
      sampler= RandomSampler(data_val),
      batch_size=32
  )

  dataloader_test = DataLoader(
      data_test,
      sampler= RandomSampler(data_test),
      batch_size=32
  )

  return dataloader_train, dataloader_val, dataloader_test

In [ ]:
def score_func(prediction, true_labels):
  """
  Функция для вычисления F1-меры между предсказанием и реальным значением
  """
  prediction_flat = np.argmax(prediction,axis=1).flatten()
  true_labels_flat = true_labels.flatten()

  f1 = f1_score(true_labels_flat, prediction_flat)

  return f1

In [ ]:
def evaluate(dataloader_val, with_additional_embeddings=False):
  """
  Функция, подсчитывающая loss и предсказания для val и test даталоадеров
  """
  model.eval()

  loss_val_total = 0
  predictions,true_vals = [],[]

  for batch in tqdm(dataloader_val):

      # если дополнительно эмбеддинги пользователей
      if with_additional_embeddings:
        b_input_ids = batch[0].to(device)
        b_input_mask = batch[1].to(device)
        b_labels = batch[2].to(device)
        b_number_feats = batch[3].to(device)

        with torch.no_grad():
          outputs = model(
              b_input_ids,
              token_type_ids=None,
              attention_mask=b_input_mask,
              labels=b_labels,
              numerical_feats=b_number_feats
              )

      # без дополнительных эмбеддингов
      else:
        batch = tuple(b.to(device) for b in batch)

        inputs = {'input_ids':  batch[0],
                  'attention_mask':batch[1],
                  'labels': batch[2]
                  }

        with torch.no_grad():
            outputs = model(**inputs)

      loss = outputs['loss'] if with_additional_embeddings else outputs[0]
      logits =  outputs['logits'] if with_additional_embeddings else outputs[1]
      loss_val_total +=loss.item()

      logits = logits.detach().cpu().numpy()
      label_ids = b_labels.cpu().numpy() if with_additional_embeddings else inputs['labels'].cpu().numpy()
      predictions.append(logits)
      true_vals.append(label_ids)

  loss_val_avg = loss_val_total/len(dataloader_val)

  predictions = np.concatenate(predictions,axis=0)
  true_vals = np.concatenate(true_vals,axis=0)

  return loss_val_avg, predictions, true_vals

In [ ]:
def train_validate(model,
                   dataloader_train, dataloader_val, dataloader_test,
                   res_dct, name,
                   num_epochs=5,
                   with_additional_embeddings=False):
  """
  Функция для обучения модели и замера качества
  """
  optimizer = AdamW(model.parameters(), lr=1e-5, eps=1e-8)

  scheduler = get_linear_schedule_with_warmup(
              optimizer,
              num_warmup_steps = 0,
              num_training_steps = len(dataloader_train)*num_epochs
  )

  res_dct[name] = {}
  res_dct[name]['train_loss'] = []
  res_dct[name]['val_loss'] = []

  for epoch in tqdm(range(1, num_epochs+1)):
    model.train()

    loss_train_total=0

    progress_bar = tqdm(dataloader_train, desc = "Epoch: {:1d}".format(epoch), leave = False, disable = False)

    for batch in progress_bar:
        model.zero_grad()

        # если дополнительно эмбеддинги пользователей
        if with_additional_embeddings:
          b_input_ids = batch[0].to(device)
          b_input_mask = batch[1].to(device)
          b_labels = batch[2].to(device)
          b_number_feats = batch[3].to(device)

          outputs = model(b_input_ids,
                          token_type_ids=None,
                          attention_mask=b_input_mask,
                          labels=b_labels,
                          numerical_feats=b_number_feats
                          )

        # без дополнительных эмбеддингов
        else:
          batch = tuple(b.to(device) for b in batch)

          inputs = {
              "input_ids": batch[0],
              "attention_mask": batch[1],
              "labels": batch[2]
          }

          outputs = model(**inputs)

        loss = outputs['loss'] if with_additional_embeddings else outputs[0]
        loss_train_total += loss.item()
        loss.backward()

        torch.nn.utils.clip_grad_norm_(model.parameters(), 1.0)

        optimizer.step()
        scheduler.step()

        progress_bar.set_postfix({'training_loss':'{:.3f}'.format(loss.item()/len(batch))})

    tqdm.write(f'\nEpoch {epoch}')

    loss_train_avg = loss_train_total/len(dataloader_train)
    tqdm.write(f'Training Loss: {loss_train_avg}')

    val_loss, val_predictions, true_vals = evaluate(dataloader_val, with_additional_embeddings)
    val_f1_score = score_func(val_predictions, true_vals)
    tqdm.write(f'Val Loss:{val_loss}\n Val F1: {val_f1_score}')

    _, test_predictions, true_test = evaluate(dataloader_test, with_additional_embeddings)
    test_f1_score = score_func(test_predictions, true_test)
    tqdm.write(f'Test F1: {test_f1_score}')

    res_dct[name]['train_loss'].append(loss_train_avg)
    res_dct[name]['val_loss'].append(val_loss)

# Модели

In [ ]:
class MLP(nn.Module):
    """
    Многослойный перцептрон с функцией активации ReLU
    Код взят отсюда - https://github.com/georgian-io/Multimodal-Toolkit/blob/master/multimodal_transformers/model/layer_utils.py
    """
    def __init__(
        self,
        input_dim,
        output_dim,
        num_hidden_lyr=2,
        dropout_prob=0.5,
        return_layer_outs=False,
        hidden_channels=None,
        bn=False,
    ):
        super().__init__()
        self.out_dim = output_dim
        self.dropout = nn.Dropout(dropout_prob)
        self.return_layer_outs = return_layer_outs
        if not hidden_channels:
            hidden_channels = [input_dim for _ in range(num_hidden_lyr)]
        elif len(hidden_channels) != num_hidden_lyr:
            raise ValueError(
                "number of hidden layers should be the same as the lengh of hidden_channels"
            )
        self.layer_channels = [input_dim] + hidden_channels + [output_dim]
        self.act_name = 'relu'
        self.activation = nn.ReLU()
        self.layers = nn.ModuleList(
            list(
                map(
                    self.weight_init,
                    [
                        nn.Linear(self.layer_channels[i], self.layer_channels[i + 1])
                        for i in range(len(self.layer_channels) - 2)
                    ],
                )
            )
        )
        final_layer = nn.Linear(self.layer_channels[-2], self.layer_channels[-1])
        self.weight_init(final_layer, activation="linear")
        self.layers.append(final_layer)

        self.bn = bn
        if self.bn:
            self.bn = nn.ModuleList(
                [torch.nn.BatchNorm1d(dim) for dim in self.layer_channels[1:-1]]
            )

    def weight_init(self, m, activation=None):
        if activation is None:
            activation = self.act_name
        torch.nn.init.xavier_uniform_(m.weight, gain=nn.init.calculate_gain(activation))
        return m

    def forward(self, x):
        """
        :param x: the input features
        :return: tuple containing output of MLP,
                and list of inputs and outputs at every layer
        """
        layer_inputs = [x]
        for i, layer in enumerate(self.layers):
            input = layer_inputs[-1]
            if layer == self.layers[-1]:
                layer_inputs.append(layer(input))
            else:
                if self.bn:
                    output = self.activation(self.bn[i](layer(input)))
                else:
                    output = self.activation(layer(input))
                layer_inputs.append(self.dropout(output))

        # model.store_layer_output(self, layer_inputs[-1])
        if self.return_layer_outs:
            return layer_inputs[-1], layer_inputs
        else:
            return layer_inputs[-1]

In [ ]:
class BertConcatFeatures(BertForSequenceClassification):
  """
  Bert с объединением числовых фичей
  """
  def __init__(self, config):
    super().__init__(config)
    self.num_labels = config.num_labels
    combined_feat_dim = config.text_feat_dim + config.numerical_feat_dim
    self.num_bn = nn.BatchNorm1d(config.numerical_feat_dim)

    dims = []
    dim = combined_feat_dim

    while True:
        dim = dim // 4
        if dim <= self.num_labels:
          break

        dims.append(int(dim))

    print('MLP layer sizes:')
    print(' Input:', combined_feat_dim)
    print(' Hidden:', dims)
    print(' Output:', self.num_labels)
    print('')

    self.mlp = MLP(combined_feat_dim,
                   self.num_labels,
                   num_hidden_lyr=len(dims),
                   dropout_prob=0.1,
                   hidden_channels=dims,
                   bn=True)

  def forward(
      self,
      input_ids=None,
      attention_mask=None,
      token_type_ids=None,
      position_ids=None,
      head_mask=None,
      inputs_embeds=None,
      labels=None,
      class_weights=None,
      output_attentions=None,
      output_hidden_states=None,
      numerical_feats=None
  ):

    outputs = self.bert(
        input_ids,
        attention_mask=attention_mask,
        token_type_ids=token_type_ids,
        head_mask=head_mask,
        inputs_embeds=inputs_embeds,
        output_attentions=output_attentions,
        output_hidden_states=output_hidden_states
    )

    cls = outputs[1]

    cls = self.dropout(cls)

    numerical_feats = self.num_bn(numerical_feats)

    combined_feats = torch.cat((cls, numerical_feats), dim=1)

    logits = self.mlp(combined_feats)

    if type(logits) is tuple:
      logits, classifier_layer_outputs = logits[0], logits[1]
    else:
      classifier_layer_outputs = [combined_feats, logits]

    if labels is not None:

      loss_fct = CrossEntropyLoss(weight=class_weights)
      labels = labels.long()
      loss = loss_fct(logits.view(-1, self.num_labels), labels.view(-1))
    else:
      loss = None

    results = {'loss': loss,
               'logits': logits,
               'classifier_layer_outputs': classifier_layer_outputs}

    return results

# BERT без каких-либо модификаций

In [ ]:
dataloader_train, dataloader_val, dataloader_test = get_dataloaders(tokenizer, 'tweet')

In [ ]:
model = BertForSequenceClassification.from_pretrained('bert-base-uncased',
                                     num_labels = 2,
                                     output_attentions = False,
                                     output_hidden_states =  False)
model.to(device);

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [ ]:
train_validate(model, dataloader_train, dataloader_val, dataloader_test, res_dct, 'without')

/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:588: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


  0%|          | 0/5 [00:00<?, ?it/s]

Epoch: 1:   0%|          | 0/2178 [00:00<?, ?it/s]


Epoch 1
Training Loss: 0.4693759312191285


  0%|          | 0/312 [00:00<?, ?it/s]

...


Epoch 5
Training Loss: 0.26540054759751286


  0%|          | 0/312 [00:00<?, ?it/s]

Val Loss:0.5342520572221241
 Val F1: 0.8362944162436549


  0%|          | 0/623 [00:00<?, ?it/s]

Test F1: 0.8387096774193549


# BERT, где в текст добавлена информация

## 1. {tweet} [SEP] The author of the text is {username}

In [ ]:
df['tweet_author_is'] = df.apply(lambda x: f'{x.tweet} [SEP] The author of the text is {x.user}', axis=1)

In [ ]:
dataloader_train, dataloader_val, dataloader_test = get_dataloaders(tokenizer, 'tweet_author_is')

In [ ]:
model = BertForSequenceClassification.from_pretrained(
    'bert-base-uncased',
    num_labels = 2,
    output_attentions = False,
    output_hidden_states =  False
    )
model.to(device);

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [ ]:
train_validate(model, dataloader_train, dataloader_val, dataloader_test, res_dct, 'tweet_author_is')

/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:588: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


  0%|          | 0/5 [00:00<?, ?it/s]

Epoch: 1:   0%|          | 0/2178 [00:00<?, ?it/s]


Epoch 1
Training Loss: 0.45909176199013646


  0%|          | 0/312 [00:00<?, ?it/s]

...


Epoch 5
Training Loss: 0.22098710621502746


  0%|          | 0/312 [00:00<?, ?it/s]

Val Loss:0.4422072132404607
 Val F1: 0.868972157586456


  0%|          | 0/623 [00:00<?, ?it/s]

Test F1: 0.8719681428743816


## 2. {tweet} [SEP] {username}

In [ ]:
df['tweet_author'] = df.apply(lambda x: f'{x.tweet} [SEP] {x.user}', axis=1)

In [ ]:
dataloader_train, dataloader_val, dataloader_test = get_dataloaders(tokenizer, 'tweet_author')

In [ ]:
model = BertForSequenceClassification.from_pretrained(
    'bert-base-uncased',
    num_labels = 2,
    output_attentions = False,
    output_hidden_states =  False
    )
model.to(device);

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [ ]:
train_validate(model, dataloader_train, dataloader_val, dataloader_test, res_dct, 'tweet_author')

/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:588: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


  0%|          | 0/5 [00:00<?, ?it/s]

Epoch: 1:   0%|          | 0/2178 [00:00<?, ?it/s]


Epoch 1
Training Loss: 0.4567935630419147


  0%|          | 0/312 [00:00<?, ?it/s]

...


Epoch 5
Training Loss: 0.21698504055211368


  0%|          | 0/312 [00:00<?, ?it/s]

Val Loss:0.4552193355794327
 Val F1: 0.8673191079736885


  0%|          | 0/623 [00:00<?, ?it/s]

Test F1: 0.8693099565706933


## 3. {tweet} [SEP] The sentiment is {positive/negative}

In [ ]:
df['tweet_sentiment_is'] = df.apply(lambda x: f"{x.tweet} [SEP] The sentiment is {'positive' if x.user == 1 else 'negative'}", axis=1)

In [ ]:
dataloader_train, dataloader_val, dataloader_test = get_dataloaders(tokenizer, 'tweet_sentiment_is')

In [ ]:
model = BertForSequenceClassification.from_pretrained(
    'bert-base-uncased',
    num_labels = 2,
    output_attentions = False,
    output_hidden_states =  False
    )
model.to(device);

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [ ]:
train_validate(model, dataloader_train, dataloader_val, dataloader_test, res_dct, 'tweet_sentiment_is')

  0%|          | 0/5 [00:00<?, ?it/s]

Epoch: 1:   0%|          | 0/2178 [00:00<?, ?it/s]


Epoch 1
Training Loss: 0.4580220839742458


  0%|          | 0/312 [00:00<?, ?it/s]

Val Loss:0.4355173653517014
 Val F1: 0.8380376878428878


...


Epoch 5
Training Loss: 0.2587067053231682


  0%|          | 0/312 [00:00<?, ?it/s]

Val Loss:0.5369047603259484
 Val F1: 0.8342092689918776


  0%|          | 0/623 [00:00<?, ?it/s]

Test F1: 0.8357575029049966


## 4. {tweet} [SEP] {positive/negative}

In [ ]:
df['tweet_sentiment'] = df.apply(lambda x: f"{x.tweet} [SEP] {'positive' if x.user == 1 else 'negative'}", axis=1)

In [ ]:
dataloader_train, dataloader_val, dataloader_test = get_dataloaders(tokenizer, 'tweet_sentiment')

In [ ]:
model = BertForSequenceClassification.from_pretrained(
    'bert-base-uncased',
    num_labels = 2,
    output_attentions = False,
    output_hidden_states =  False
    )
model.to(device);

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [ ]:
train_validate(model, dataloader_train, dataloader_val, dataloader_test, res_dct, 'tweet_sentiment')

/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:588: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


  0%|          | 0/5 [00:00<?, ?it/s]

Epoch: 1:   0%|          | 0/2178 [00:00<?, ?it/s]


Epoch 1
Training Loss: 0.4735045466979126


  0%|          | 0/312 [00:00<?, ?it/s]

...


Epoch 5
Training Loss: 0.2676806150190703


  0%|          | 0/312 [00:00<?, ?it/s]

Val Loss:0.5290178026621922
 Val F1: 0.8330536242308001


  0%|          | 0/623 [00:00<?, ?it/s]

Test F1: 0.8336347923951928


# BERT с использованием эмбеддингов пользователей

## Эмбеддинги, полученные с помощью LDA

In [ ]:
keys = ['post_lda_2', 'post_lda_5', 'post_lda_10', 'post_lda_20',
        'user_lda_2', 'user_lda_5', 'user_lda_10', 'user_lda_20']

In [ ]:
for key in keys:
  print(key)

  # выбираем соответствующий словарь
  tmp_dct = knowledge_dct[key]
  user_embedding_dim = int(key.split('_')[-1])

  # создаем даталоадеры с учетом эмбеддингов для пользователей
  dataloader_train, dataloader_val, dataloader_test = get_dataloaders(tokenizer, 'tweet',
                                                                      knowledge_dct=tmp_dct,
                                                                      user_embedding_dim=user_embedding_dim)

  # подготоваливаем модель
  config = BertConfig.from_pretrained(
      'bert-base-uncased',
      num_labels=2
      )

  config.numerical_feat_dim = user_embedding_dim
  config.text_feat_dim = 768 # потому что в BERT размерность скрытого слоя - 768

  model = BertConcatFeatures.from_pretrained(
      'bert-base-uncased',
      config=config
      )

  model.to(device)

  # обучаем уже на 10 эпохах
  train_validate(model, dataloader_train, dataloader_val, dataloader_test, res_dct, key,
                 num_epochs=10, with_additional_embeddings=True)

post_lda_2


/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
Some weights of BertConcatFeatures were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight', 'mlp.bn.0.bias', 'mlp.bn.0.num_batches_tracked', 'mlp.bn.0.running_mean', 'mlp.bn.0.running_var', 'mlp.bn.0.weight', 'mlp.bn.1.bias', 'mlp.bn.1.num_batches_tracked', 'mlp.bn.1.running_mean', 'mlp.bn.1.running_var', 'mlp.bn.1.weight', 'mlp.bn.2.bias', 'mlp.bn.2.num_batches_tracked', 'mlp.bn.2.running_mean', 'mlp.bn.2.running_var', 'mlp.bn.2.weight', 'mlp.bn.3.bias', 'mlp.bn.3.num_batches_tracked', 'mlp.bn.3.running_mean', 'mlp.bn.3.running_var', 'mlp.bn.3.weight', 'mlp.layers.0.bias', 'mlp.layers.0.weight', 'mlp.layers.1.bias', 'mlp.layers.

MLP layer sizes:
 Input: 770
 Hidden: [192, 48, 12, 3]
 Output: 2



/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:588: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


  0%|          | 0/10 [00:00<?, ?it/s]

...


Epoch 10
Training Loss: 0.5670834448876131


  0%|          | 0/312 [00:00<?, ?it/s]

Val Loss:0.6085203091303507
 Val F1: 0.8390509294242103


  0%|          | 0/623 [00:00<?, ?it/s]

Test F1: 0.8423807898031181


## Эмбеддинги, полученные с помощью Word2Vec / GloVe

In [ ]:
keys = ['glove_100', 'glove_200', 'w2v_300']

In [ ]:
for key in keys:
  print(key)

  # выбираем соответствующий словарь
  tmp_dct = knowledge_dct[key]
  user_embedding_dim = int(key.split('_')[-1])

  # создаем даталоадеры с учетом эмбеддингов для пользователей
  dataloader_train, dataloader_val, dataloader_test = get_dataloaders(tokenizer, 'tweet',
                                                                      knowledge_dct=tmp_dct,
                                                                      user_embedding_dim=user_embedding_dim)

  # подготоваливаем модель
  config = BertConfig.from_pretrained(
      'bert-base-uncased',
      num_labels=2
      )

  config.numerical_feat_dim = user_embedding_dim
  config.text_feat_dim = 768 # потому что в BERT размерность скрытого слоя - 768

  model = BertConcatFeatures.from_pretrained(
      'bert-base-uncased',
      config=config
      )

  model.to(device)

  # обучаем уже на 10 эпохах
  train_validate(model, dataloader_train, dataloader_val, dataloader_test, res_dct, key,
                 num_epochs=10, with_additional_embeddings=True)

glove_100


/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
Some weights of BertConcatFeatures were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight', 'mlp.bn.0.bias', 'mlp.bn.0.num_batches_tracked', 'mlp.bn.0.running_mean', 'mlp.bn.0.running_var', 'mlp.bn.0.weight', 'mlp.bn.1.bias', 'mlp.bn.1.num_batches_tracked', 'mlp.bn.1.running_mean', 'mlp.bn.1.running_var', 'mlp.bn.1.weight', 'mlp.bn.2.bias', 'mlp.bn.2.num_batches_tracked', 'mlp.bn.2.running_mean', 'mlp.bn.2.running_var', 'mlp.bn.2.weight', 'mlp.bn.3.bias', 'mlp.bn.3.num_batches_tracked', 'mlp.bn.3.running_mean', 'mlp.bn.3.running_var', 'mlp.bn.3.weight', 'mlp.layers.0.bias', 'mlp.layers.0.weight', 'mlp.layers.1.bias', 'mlp.layers.

MLP layer sizes:
 Input: 868
 Hidden: [217, 54, 13, 3]
 Output: 2



/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:588: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


  0%|          | 0/10 [00:00<?, ?it/s]

...


Epoch 10
Training Loss: 0.503768394076025


  0%|          | 0/312 [00:00<?, ?it/s]

Val Loss:0.5533126458907739
 Val F1: 0.8461712903469649


  0%|          | 0/623 [00:00<?, ?it/s]

Test F1: 0.8467435858509186


## Эмбеддинги, полученные с помощью BERT

In [ ]:
key = 'bert'
user_embedding_dim = 768

print(key)

# выбираем соответствующий словарь
tmp_dct = knowledge_dct[key]

# создаем даталоадеры с учетом эмбеддингов для пользователей
dataloader_train, dataloader_val, dataloader_test = get_dataloaders(tokenizer, 'tweet',
                                                                    knowledge_dct=tmp_dct,
                                                                    user_embedding_dim=user_embedding_dim)

# подготоваливаем модель
config = BertConfig.from_pretrained(
    'bert-base-uncased',
    num_labels=2
    )

config.numerical_feat_dim = user_embedding_dim
config.text_feat_dim = 768 # потому что в BERT размерность скрытого слоя - 768

model = BertConcatFeatures.from_pretrained(
    'bert-base-uncased',
    config=config
    )

model.to(device)

# обучаем уже на 10 эпохах
train_validate(model, dataloader_train, dataloader_val, dataloader_test, res_dct, key,
                num_epochs=10, with_additional_embeddings=True)

bert


/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
Some weights of BertConcatFeatures were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight', 'mlp.bn.0.bias', 'mlp.bn.0.num_batches_tracked', 'mlp.bn.0.running_mean', 'mlp.bn.0.running_var', 'mlp.bn.0.weight', 'mlp.bn.1.bias', 'mlp.bn.1.num_batches_tracked', 'mlp.bn.1.running_mean', 'mlp.bn.1.running_var', 'mlp.bn.1.weight', 'mlp.bn.2.bias', 'mlp.bn.2.num_batches_tracked', 'mlp.bn.2.running_mean', 'mlp.bn.2.running_var', 'mlp.bn.2.weight', 'mlp.bn.3.bias', 'mlp.bn.3.num_batches_tracked', 'mlp.bn.3.running_mean', 'mlp.bn.3.running_var', 'mlp.bn.3.weight', 'mlp.layers.0.bias', 'mlp.layers.0.weight', 'mlp.layers.1.bias', 'mlp.layers.

MLP layer sizes:
 Input: 1536
 Hidden: [384, 96, 24, 6]
 Output: 2



/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:588: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


  0%|          | 0/10 [00:00<?, ?it/s]

...


Epoch 10
Training Loss: 0.44965921157647754


  0%|          | 0/312 [00:00<?, ?it/s]

Val Loss:0.5084861872287897
 Val F1: 0.8515774196012529


  0%|          | 0/623 [00:00<?, ?it/s]

Test F1: 0.851513990034496


# BERT, где в текст добавлена информация + эмбеддинги, полученные с помощью BERT

## 1. {tweet} [SEP] The author of the text is {username}

In [ ]:
df['tweet_author_is'] = df.apply(lambda x: f'{x.tweet} [SEP] The author of the text is {x.user}', axis=1)

In [ ]:
key_for_res_dct = 'tweet_author_is_bert'
key_for_knowledge_dct = 'bert'
user_embedding_dim = 768

print(key)

# выбираем соответствующий словарь
tmp_dct = knowledge_dct[key_for_knowledge_dct]

# создаем даталоадеры с учетом эмбеддингов для пользователей
dataloader_train, dataloader_val, dataloader_test = get_dataloaders(tokenizer, 'tweet_author_is',
                                                                    knowledge_dct=tmp_dct,
                                                                    user_embedding_dim=user_embedding_dim)

# подготоваливаем модель
config = BertConfig.from_pretrained(
    'bert-base-uncased',
    num_labels=2
    )

config.numerical_feat_dim = user_embedding_dim
config.text_feat_dim = 768 # потому что в BERT размерность скрытого слоя - 768

model = BertConcatFeatures.from_pretrained(
    'bert-base-uncased',
    config=config
    )

model.to(device)

# обучаем уже на 10 эпохах
train_validate(model, dataloader_train, dataloader_val, dataloader_test, res_dct, key_for_res_dct,
               num_epochs=10, with_additional_embeddings=True)

tweet_author_is_bert


/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
Some weights of BertConcatFeatures were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight', 'mlp.bn.0.bias', 'mlp.bn.0.num_batches_tracked', 'mlp.bn.0.running_mean', 'mlp.bn.0.running_var', 'mlp.bn.0.weight', 'mlp.bn.1.bias', 'mlp.bn.1.num_batches_tracked', 'mlp.bn.1.running_mean', 'mlp.bn.1.running_var', 'mlp.bn.1.weight', 'mlp.bn.2.bias', 'mlp.bn.2.num_batches_tracked', 'mlp.bn.2.running_mean', 'mlp.bn.2.running_var', 'mlp.bn.2.weight', 'mlp.bn.3.bias', 'mlp.bn.3.num_batches_tracked', 'mlp.bn.3.running_mean', 'mlp.bn.3.running_var', 'mlp.bn.3.weight', 'mlp.layers.0.bias', 'mlp.layers.0.weight', 'mlp.layers.1.bias', 'mlp.layers.

MLP layer sizes:
 Input: 1536
 Hidden: [384, 96, 24, 6]
 Output: 2



/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:588: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


  0%|          | 0/10 [00:00<?, ?it/s]

...


Epoch 10
Training Loss: 0.44327417132337776


  0%|          | 0/312 [00:00<?, ?it/s]

Val Loss:0.5007401148860271
 Val F1: 0.8679571923197986


  0%|          | 0/623 [00:00<?, ?it/s]

Test F1: 0.8728886793935108


## 2. {tweet} [SEP] {username}

In [ ]:
df['tweet_author'] = df.apply(lambda x: f'{x.tweet} [SEP] {x.user}', axis=1)

In [ ]:
key_for_res_dct = 'tweet_author_bert'
key_for_knowledge_dct = 'bert'
user_embedding_dim = 768

print(key)

# выбираем соответствующий словарь
tmp_dct = knowledge_dct[key_for_knowledge_dct]

# создаем даталоадеры с учетом эмбеддингов для пользователей
dataloader_train, dataloader_val, dataloader_test = get_dataloaders(tokenizer, 'tweet_author',
                                                                    knowledge_dct=tmp_dct,
                                                                    user_embedding_dim=user_embedding_dim)

# подготоваливаем модель
config = BertConfig.from_pretrained(
    'bert-base-uncased',
    num_labels=2
    )

config.numerical_feat_dim = user_embedding_dim
config.text_feat_dim = 768 # потому что в BERT размерность скрытого слоя - 768

model = BertConcatFeatures.from_pretrained(
    'bert-base-uncased',
    config=config
    )

model.to(device)

# обучаем уже на 10 эпохах
# увеличиваем lr, потому что внутри MLP
train_validate(model, dataloader_train, dataloader_val, dataloader_test, res_dct, key_for_res_dct,
               num_epochs=10, with_additional_embeddings=True)

tweet_author_is_bert


/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
Some weights of BertConcatFeatures were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight', 'mlp.bn.0.bias', 'mlp.bn.0.num_batches_tracked', 'mlp.bn.0.running_mean', 'mlp.bn.0.running_var', 'mlp.bn.0.weight', 'mlp.bn.1.bias', 'mlp.bn.1.num_batches_tracked', 'mlp.bn.1.running_mean', 'mlp.bn.1.running_var', 'mlp.bn.1.weight', 'mlp.bn.2.bias', 'mlp.bn.2.num_batches_tracked', 'mlp.bn.2.running_mean', 'mlp.bn.2.running_var', 'mlp.bn.2.weight', 'mlp.bn.3.bias', 'mlp.bn.3.num_batches_tracked', 'mlp.bn.3.running_mean', 'mlp.bn.3.running_var', 'mlp.bn.3.weight', 'mlp.layers.0.bias', 'mlp.layers.0.weight', 'mlp.layers.1.bias', 'mlp.layers.

MLP layer sizes:
 Input: 1536
 Hidden: [384, 96, 24, 6]
 Output: 2



/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:588: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


  0%|          | 0/10 [00:00<?, ?it/s]

...


Epoch 10
Training Loss: 0.4281331981344985


  0%|          | 0/312 [00:00<?, ?it/s]

Val Loss:0.48966694384431225
 Val F1: 0.8695855771482088


  0%|          | 0/623 [00:00<?, ?it/s]

Test F1: 0.8694058942772493


In [ ]:
# сохраним словарь
with open('res.pickle', 'wb') as f:
  pickle.dump(res_dct, f)